## Load Model From huggingface

In [1]:
import os

#os.environ["CUDA_VISIBLE_DEVICES"]="0"
#os.environ["https_proxy"] = 'http://127.0.0.1:7890'
#os.environ["http_proxy"] = 'http://127.0.0.1:7890'

from transformers import AutoTokenizer, AutoModel,AutoConfig
import torch
device = 'cuda'
checkpoint = "THUDM/chatglm-6b"
tokenizer = AutoTokenizer.from_pretrained("/home/data/ChatGLM/model", trust_remote_code=True)
model = AutoModel.from_pretrained("/home/data/ChatGLM/model", trust_remote_code=True).half().cuda()
model.eval()
# config=AutoConfig.from_pretrained("/home/data/ChatGLM/model", trust_remote_code=True)
# print(config.eos_token_id)

/root/miniconda3/envs/llm/lib/python3.10/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
Explicitly passing a `revision` is encouraged when loading a model with custom code to ensure no malicious code has been contributed in a newer revision.
Explicitly passing a `revision` is encouraged when loading a configuration with custom code to ensure no malicious code has been contributed in a newer revision.
Explicitly passing a `revision` is encouraged when loading a model with custom code to ensure no malicious code has been contributed in a newer revision.
Loading checkpoint shards: 100%|██████████| 8/8 [00:11<00:00,  1.44s/it]


ChatGLMForConditionalGeneration(
  (transformer): ChatGLMModel(
    (word_embeddings): Embedding(130528, 4096)
    (layers): ModuleList(
      (0): GLMBlock(
        (input_layernorm): LayerNorm((4096,), eps=1e-05, elementwise_affine=True)
        (attention): SelfAttention(
          (rotary_emb): RotaryEmbedding()
          (query_key_value): Linear(in_features=4096, out_features=12288, bias=True)
          (dense): Linear(in_features=4096, out_features=4096, bias=True)
        )
        (post_attention_layernorm): LayerNorm((4096,), eps=1e-05, elementwise_affine=True)
        (mlp): GLU(
          (dense_h_to_4h): Linear(in_features=4096, out_features=16384, bias=True)
          (dense_4h_to_h): Linear(in_features=16384, out_features=4096, bias=True)
        )
      )
      (1): GLMBlock(
        (input_layernorm): LayerNorm((4096,), eps=1e-05, elementwise_affine=True)
        (attention): SelfAttention(
          (rotary_emb): RotaryEmbedding()
          (query_key_value): Linear(i

In [5]:
lora_config = {
        'r': 32,
        'lora_alpha':32,
        'lora_dropout':0.1,
        'enable_lora':[True, True, True],
    }

## Insert LoRA to model

In [6]:
import loralib as lora
from lora_utils.insert_lora import get_lora_model


===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please submit your error trace to: https://github.com/TimDettmers/bitsandbytes/issues


In [7]:
lora_config = {
    'r': 32,
    'lora_alpha':32,
    'lora_dropout':0.05,
    'enable_lora':[True, False, True],
}
# model = ChatGLMForConditionalGeneration.from_pretrained(args.model_dir)

In [8]:
model = get_lora_model(model, lora_config)


100%|██████████| 28/28 [00:33<00:00,  1.20s/it]

trainable_params:14680064 (0.24%), non_trainable_params:6173286400


In [9]:
model.load_state_dict(torch.load('saved/finetune_test/finetune_test_epoch_0.pt'), strict=False)
model.eval()

ChatGLMForConditionalGeneration(
  (transformer): ChatGLMModel(
    (word_embeddings): Embedding(130528, 4096)
    (layers): ModuleList(
      (0): GLMBlock(
        (input_layernorm): LayerNorm((4096,), eps=1e-05, elementwise_affine=True)
        (attention): SelfAttention(
          (rotary_emb): RotaryEmbedding()
          (query_key_value): LoraModel(
            (model): QKV_layer(
              (linear_q): Linear(
                in_features=4096, out_features=4096, bias=True
                (lora_dropout): Dropout(p=0.05, inplace=False)
                (lora_A): Linear(in_features=4096, out_features=32, bias=False)
                (lora_B): Linear(in_features=32, out_features=4096, bias=False)
              )
              (linear_k): Linear(in_features=4096, out_features=4096, bias=True)
              (linear_v): Linear(
                in_features=4096, out_features=4096, bias=True
                (lora_dropout): Dropout(p=0.05, inplace=False)
                (lora_A): Linear(

## Dataset

In [2]:
device = 'cuda'
# model.half().to(device)

In [3]:
import dataset.GLM 
from torch.utils.data import DataLoader

dataset.GLM.device = device
#dataset.GLM.pad_to = 8

In [26]:
pairs = [{'prompt':'你好', 'completion':'你好, 我是ChatGLM'}]
pairs_encoded = dataset.GLM.encode_pairs(pairs, tokenizer)
train_dataset = dataset.GLM.SimpleDataset(pairs_encoded)
train_dataloader = DataLoader(dataset=train_dataset, collate_fn = dataset.GLM.collate_fn, shuffle=True, batch_size=1)

## Training

In [ ]:
model.half().to(device)

In [27]:
batch = {k: v.to(device) for k, v in next(iter(train_dataloader)).items()}

In [28]:
model(**batch).loss

tensor(2.8086, device='cuda:0', dtype=torch.float16, grad_fn=<ToCopyBackward0>)

## Inference

In [4]:
import dataset.Alpaca
model.eval()

ChatGLMForConditionalGeneration(
  (transformer): ChatGLMModel(
    (word_embeddings): Embedding(130528, 4096)
    (layers): ModuleList(
      (0): GLMBlock(
        (input_layernorm): LayerNorm((4096,), eps=1e-05, elementwise_affine=True)
        (attention): SelfAttention(
          (rotary_emb): RotaryEmbedding()
          (query_key_value): Linear(in_features=4096, out_features=12288, bias=True)
          (dense): Linear(in_features=4096, out_features=4096, bias=True)
        )
        (post_attention_layernorm): LayerNorm((4096,), eps=1e-05, elementwise_affine=True)
        (mlp): GLU(
          (dense_h_to_4h): Linear(in_features=4096, out_features=16384, bias=True)
          (dense_4h_to_h): Linear(in_features=16384, out_features=4096, bias=True)
        )
      )
      (1): GLMBlock(
        (input_layernorm): LayerNorm((4096,), eps=1e-05, elementwise_affine=True)
        (attention): SelfAttention(
          (rotary_emb): RotaryEmbedding()
          (query_key_value): Linear(i

In [18]:
# pairs = [
#     {'prompt':'周末适合哪里玩?', 'completion':'周末适合去上海'},
#     {'prompt':'周末适合哪里玩?', 'completion':'周末适合去北京'},
# ]
import random
test_pairs= dataset.Alpaca.load('./data/LCCC-base_test.json')
random.shuffle(test_pairs)
completion=[i['completion'] for i in test_pairs]
print(test_pairs)
pairs_encoded = dataset.GLM.encode_pairs(test_pairs[:200], tokenizer, with_eos=False)
test_dataset = dataset.GLM.SimpleDataset(pairs_encoded)
BATCH_SIZE=15
test_dataloader = DataLoader(dataset=test_dataset, collate_fn = dataset.GLM.collate_fn, shuffle=False, batch_size=BATCH_SIZE)
len(test_dataloader)

[{'prompt': '假设你是一名中国科学院大学（国科大）南京学院的2022级研究生，以下的聊天记录来自你与你的家人或朋友。请根据聊天记录给出相应贴切的回答，要求回答接地气，口语化。\n\n### 聊天记录:\n奥特曼等你回邢台了我们也要去吃好吃滴哇哈哈哈哈哈阿哈哈哈哈哈哈\n\n### 你的回答:', 'completion': '好啊去石家庄也要吃'}, {'prompt': '假设你是一名中国科学院大学（国科大）南京学院的2022级研究生，以下的聊天记录来自你与你的家人或朋友。请根据聊天记录给出相应贴切的回答，要求回答接地气，口语化。\n\n### 聊天记录:\n你好旧时光1-26已泄露，炒鸡好看，我斯我自娶，不要一分\n\n### 你的回答:', 'completion': '真的假的'}, {'prompt': '假设你是一名中国科学院大学（国科大）南京学院的2022级研究生，以下的聊天记录来自你与你的家人或朋友。请根据聊天记录给出相应贴切的回答，要求回答接地气，口语化。\n\n### 聊天记录:\n广东人表示青菜不能随便，不能随便，不能随便\n\n### 你的回答:', 'completion': '哈哈哈反正，我只管炒，我不吃。'}, {'prompt': '假设你是一名中国科学院大学（国科大）南京学院的2022级研究生，以下的聊天记录来自你与你的家人或朋友。请根据聊天记录给出相应贴切的回答，要求回答接地气，口语化。\n\n### 聊天记录:\n你在等签名？\n没去啊哈哈怕迟到来不及\n到几点呀，你那么早回去？\n不知道我要准备很多东西然后赶校车\n校车几点到，到你家？\n\n### 你的回答:', 'completion': '附近18：00'}, {'prompt': '假设你是一名中国科学院大学（国科大）南京学院的2022级研究生，以下的聊天记录来自你与你的家人或朋友。请根据聊天记录给出相应贴切的回答，要求回答接地气，口语化。\n\n### 聊天记录:\n嗲是什么意思啊？\n上海话，非常美妙的意思\n\n### 你的回答:', 'completion': '噢，我还以为你是在撒娇'}, {'prompt': '假设你是一名中国科学院大学（国科大）南京学院的2022级研究生，以下的聊天记录来自你与你的家人或朋友。请根据聊天记录给出相应贴切的回答

14

In [20]:
import json
import tqdm
import re
result=[]
pbar = tqdm.tqdm(total=len(test_dataloader))
with open('result.json', 'w', encoding='utf-8') as f:
    for i,batch in enumerate(test_dataloader):
        batch = {k: v.to(device) for k, v in batch.items()}
        outputs=model.generate(
        **batch, 
        max_length=1024,
        eos_token_id=130005,
        do_sample=True,
        temperature=0.9,
        top_p = 0.75,
        top_k = 10000,
        repetition_penalty=1.5, 
        num_return_sequences=1,
        )
        templ=[{'completion':completion[i*BATCH_SIZE+j:i*BATCH_SIZE+j+1]} for j in range(BATCH_SIZE)]
        for j,output in enumerate(outputs):
            pattern = r'[^\u4e00-\u9fa5a-zA-Z0-9。，！？“”‘’,."!?\[\]@#$%&*()（）【】<>《》{}~\-——+=|:;；：、|]'
            text = re.sub(pattern, '', tokenizer.sp_tokenizer.decode(output).split('你的回答: ')[-1])
            templ[j]['response']=text
        result+=templ
        pbar.update(1)
    f.write(json.dumps(result, ensure_ascii=False, indent=4))
    pbar.close()

 36%|███▌      | 5/14 [00:17<00:30,  3.41s/it]
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.


In [16]:
from nltk.translate.bleu_score import sentence_bleu
import jieba
def calculate_bleu_score(reference, candidate):
    reference_tokens = jieba.cut(reference)
    candidate_tokens = jieba.cut(candidate)
    
    # Convert the tokenized sentences into lists of tokens
    reference_tokens = list(reference_tokens)
    candidate_tokens = list(candidate_tokens)
    
    # Calculate the BLEU score
    bleu_score = sentence_bleu([reference_tokens], candidate_tokens)
    
    return bleu_score
b_l=[]
with open('result.json', 'w', encoding='utf-8') as f:
    result=json.load(f)
    for d in result:
        d['bleu']=calculate_bleu_score(d['completion'],d['response'])
    b_l.append(d['bleu'])
print('Mean BLEU score:', sum(b_l)/len(b_l))

UnsupportedOperation: not readable

AttributeError: 'DataLoader' object has no attribute 'to'

In [31]:
batch = {k: v.to(device) for k, v in next(iter(test_dataloader)).items()}
print(len(batch))

4


In [32]:
outputs = model.generate(
    **batch, 
    max_length=1024,
    eos_token_id=130005,
    do_sample=True,
    temperature=0.7,
    top_p = 0.75,
    top_k = 10000,
    repetition_penalty=1.5, 
    num_return_sequences=1,

    )

A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.


In [ ]:
for output in outputs:
    print(tokenizer.sp_tokenizer.decode(output))

## Chat

In [7]:

from dataset.Alpaca import load
test_pairs= load('./data/train_2.json')
print(test_pairs[0])

{'prompt': '假设你是一名中国科学院大学（国科大）南京学院的2022级研究生，以下的聊天记录来自你与你的家人或朋友。请根据聊天记录给出相应贴切的回答，要求回答接地气，口语化。\n\n### 聊天记录:\n听说过詹姆斯·麦斯登这个人吗？\n\n### 你的回答:', 'completion': '是的，他是一位美国人。'}


In [21]:
i=4
print(test_pairs[i]['prompt'])
response, history = model.chat(tokenizer, '你好啊，你叫什么名字？', history=[])

The dtype of attention mask (torch.int64) is not bool


假设你是一名中国科学院大学（国科大）南京学院的2022级研究生，以下的聊天记录来自你与你的家人或朋友。请根据聊天记录给出相应贴切的回答，要求回答接地气，口语化。

### 聊天记录:
听说过南宝拉这个人吗？
是的，听说过一些，她是韩国人。
对呀，她是做什么的呀？
她是一名演员呀，你不知道她吗？
啊，想起来了她好像是2006年出道的。

### 你的回答:


In [22]:
print('completion: ',test_pairs[i]['completion'])
print('response: ',response)

completion:  对呀，出道作品是以微笑的面孔回望，知道她是哪年出生的吗？
response:  你好呀，我是一名虚拟语气词。


## Load pretrain weight

In [97]:
model.load_state_dict(torch.load('saved/chatglm-6b_alpaca_5.pt'), strict=False)

_IncompatibleKeys(missing_keys=['transformer.word_embeddings.weight', 'transformer.layers.0.input_layernorm.weight', 'transformer.layers.0.input_layernorm.bias', 'transformer.layers.0.attention.query_key_value.model.linear_q.weight', 'transformer.layers.0.attention.query_key_value.model.linear_q.bias', 'transformer.layers.0.attention.query_key_value.model.linear_k.weight', 'transformer.layers.0.attention.query_key_value.model.linear_k.bias', 'transformer.layers.0.attention.query_key_value.model.linear_v.weight', 'transformer.layers.0.attention.query_key_value.model.linear_v.bias', 'transformer.layers.0.attention.dense.weight', 'transformer.layers.0.attention.dense.bias', 'transformer.layers.0.post_attention_layernorm.weight', 'transformer.layers.0.post_attention_layernorm.bias', 'transformer.layers.0.mlp.dense_h_to_4h.weight', 'transformer.layers.0.mlp.dense_h_to_4h.bias', 'transformer.layers.0.mlp.dense_4h_to_h.weight', 'transformer.layers.0.mlp.dense_4h_to_h.bias', 'transformer.layer